In [17]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from statsmodels.tsa.stattools import adfuller, kpss
from statsmodels.tsa.arima.model import ARIMA
from statsmodels.graphics.tsaplots import plot_acf, plot_pacf

#### 1. Visualising MACD

In [65]:
# Importing data 

btc_prices = pd.read_csv("processed_data/BTC_1m_data_indicators.csv")
eth_prices = pd.read_csv("processed_data/BTC_1m_data_indicators.csv")
xrp_prices =  pd.read_csv("processed_data/XRP_1m_data_indicators.csv")
solana_prices =  pd.read_csv("processed_data/SOL_1m_data_indicators.csv")

In [3]:
# Function to plot the prices of last 60 minutes from running this script

def last_60_minutes(crypto_prices):
    crypto_prices['Open Time'] = pd.to_datetime(crypto_prices['Open Time'], format='%Y-%m-%d %H:%M:%S')

    starting_from = crypto_prices['Open Time'].max() - pd.Timedelta(minutes = 60)
    last_60_min = crypto_prices[crypto_prices['Open Time'] >= starting_from]
    # Create the figure
    fig = go.Figure()

    # Add MACD line
    fig.add_trace(go.Scatter(x=last_60_min['Open Time'], y=last_60_min['MACD'], mode='lines', name='MACD', line=dict(color='#1e81b0')))

    # Add Signal line
    fig.add_trace(go.Scatter(x=last_60_min['Open Time'], y=last_60_min['MACD_Signal'], mode='lines', name='Signal Line', line=dict(color='#CC5137')))

    # Add Histogram
    fig.add_trace(go.Bar(x=last_60_min['Open Time'], y=last_60_min['MACD_Hist'], name='Histogram', marker=dict(color='gray', opacity=0.3)))

    # Update layout (title, labels, etc.)
    fig.update_layout(
        title='MACD Indicator',
        xaxis_title='Time',
        yaxis_title='Price (USD)',
        template='ggplot2', 
        xaxis_rangeslider_visible=True
    )

    # Show the plot
    fig.show()

In [4]:
last_60_minutes(btc_prices)

In [5]:
last_60_minutes(eth_prices)

In [6]:
last_60_minutes(xrp_prices)

In [7]:
last_60_minutes(solana_prices)

#### 2. Checking Stationarity

In [66]:
test_data = btc_prices[:-20]

In [67]:
test_data

Open Time      Open      High       Low     Close    Volume  \
0      2024-12-31 16:00:00  95412.00  95454.55  95308.00  95308.01  15.17924   
1      2024-12-31 16:01:00  95308.01  95386.03  95291.66  95361.49  17.54599   
2      2024-12-31 16:02:00  95361.48  95373.81  95320.27  95352.26  10.70271   
3      2024-12-31 16:03:00  95352.26  95364.48  95250.00  95258.62  11.82793   
4      2024-12-31 16:04:00  95258.61  95304.37  95201.78  95272.29  19.69380   
...                    ...       ...       ...       ...       ...       ...   
84936  2025-02-28 15:36:00  83936.91  84035.21  83786.95  83839.19  55.59111   
84937  2025-02-28 15:37:00  83839.18  83979.94  83760.06  83979.94  86.41404   
84938  2025-02-28 15:38:00  83980.00  84159.99  83935.95  83971.08  69.68609   
84939  2025-02-28 15:39:00  83972.05  83999.42  83733.00  83733.00  69.61557   
84940  2025-02-28 15:40:00  83733.00  83868.00  83708.01  83865.99  54.82723   

       Number of Trades Coin          MACD   MACD_Signal  MACD_Hist  \
0                  4110  BTC  95308.010000  95308.010000   0.000000   
1                  3991  BTC  95316.237692  95318.706000  -2.468308   
2                  2292  BTC  95321.779586  95325.416800  -3.637214   
3                  4267  BTC  95312.062726  95312.057440   0.005286   
4                  5153  BTC  95305.943845  95304.103952   1.839893   
...                 ...  ...           ...           ...        ...   
84936             11593  BTC    256.977560    337.757821 -80.780260   
84937              9024  BTC    239.219602    318.050177 -78.830575   
84938              9519  BTC    221.873741    298.814890 -76.941149   
84939              9571  BTC    186.763067    276.404525 -89.641458   
84940              9879  BTC    167.735239    254.670668 -86.935429   

                RSI  
0      95308.010000  
1      95334.750000  
2      95340.586667  
3      95320.095000  
4      95310.534000  
...             ...  
84936     55.339777  
84937     59.330354  
84938     58.973132  
84939     50.222588  
84940     54.301666  

[84941 rows x 12 columns]

In [63]:
# Perform ADF test on the original data
adf_test = adfuller(test_data['Close'].dropna())
print(f"ADF Statistic: {adf_test[0]}")
print(f"p-value: {adf_test[1]}")
print(f"Critical Values: {adf_test[4]}")

# Perform KPSS test on the original data
kpss_test = kpss(test_data['Close'].dropna(), regression='c')
print(f"KPSS Statistic: {kpss_test[0]}")
print(f"p-value: {kpss_test[1]}")


ADF Statistic: -1.120943737688649
p-value: 0.7066479332700726
Critical Values: {'1%': -3.430427912407388, '5%': -2.8615744359907795, '10%': -2.5667883290855524}
KPSS Statistic: 10.440824986882845
p-value: 0.01


/var/folders/9d/bxxrjx5d1qg5y0x87t0hp84w0000gn/T/ipykernel_12715/66006148.py:8: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the p-value returned.




Both tests suggest non-stationarity of the prices time series, which is exactly what we expect.

In [68]:

# If the series is non-stationary, difference it
data_diff = test_data['Close'].diff().dropna()

# Create an interactive plot for the differenced data
fig_diff = go.Figure()

fig_diff.add_trace(go.Scatter(x=test_data['Open Time'], y=data_diff, mode='lines', name='Differenced Price'))
fig_diff.update_layout(
    title="Differenced Cryptocurrency Price",
    xaxis_title="Date",
    yaxis_title="Differenced Price",
    template="ggplot2"
)

fig_diff.show()

In [69]:
# Perform ADF test on the differenced data
adf_test_diff = adfuller(data_diff)
print(f"ADF Statistic (Differenced Data): {adf_test_diff[0]}")
print(f"p-value (Differenced Data): {adf_test_diff[1]}")

ADF Statistic (Differenced Data): -37.78937863765132
p-value (Differenced Data): 0.0


The difference could be stationary, which corresponds to what we see on the graph as well.

We shall try fitting an ARIMA(1,1,1) model on the data.

In [70]:
test_data.set_index('Open Time', inplace = True)

In [71]:
# Step 2: Ensure 'Close' column is numeric (in case it's not)
test_data['Close'] = pd.to_numeric(test_data['Close'], errors='coerce')  # Convert to numeric, force errors to NaN

/var/folders/9d/bxxrjx5d1qg5y0x87t0hp84w0000gn/T/ipykernel_12715/3585757055.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [72]:
data_diff_reset = data_diff.reset_index(drop=True)
# Fit ARIMA model (p=1, d=1, q=1)
model = ARIMA(data_diff_reset, order=(1, 1, 1))
model_fit = model.fit()


# Step 3: Print the summary of the model
print(model_fit.summary())

# Step 4: Make predictions (forecasting)
forecast_steps = 1
  # Predict the next minute
forecast_diff = model_fit.forecast(steps=forecast_steps)

# Create a time index for the forecast
forecast_index = pd.date_range(start=test_data.index[-1], periods=forecast_steps + 1, freq='T')[1:]
# Reconstruct the forecasted values to the original scale
forecast_original = test_data['Close'].iloc[-1] + np.cumsum(forecast_diff)  # Add the forecasted difference to the last actual price



                               SARIMAX Results                                
Dep. Variable:                  Close   No. Observations:                84940
Model:                 ARIMA(1, 1, 1)   Log Likelihood             -487422.655
Date:                Sun, 09 Mar 2025   AIC                         974851.310
Time:                        19:40:37   BIC                         974879.359
Sample:                             0   HQIC                        974859.885
                              - 84940                                         
Covariance Type:                  opg                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
ar.L1         -0.0081      0.001     -8.112      0.000      -0.010      -0.006
ma.L1         -0.9999   5.78e-05  -1.73e+04      0.000      -1.000      -1.000
sigma2      5648.9322      6.150    918.535      0.0

In [76]:
if test_data['Close'].iloc[-1] < forecast_original.iloc[0]:
    print(f"The price will increase from ${test_data['Close'].iloc[-1]} to ${forecast_original.iloc[0]}")
elif test_data['Close'].iloc[-1] > forecast_original.iloc[0]:
    print(f"The price will decrease from ${test_data['Close'].iloc[-1]} to ${forecast_original.iloc[0]}")

The price will decrease from $83865.99 to $83864.31580544222


In [75]:
btc_prices[-21:]

Open Time      Open      High       Low     Close    Volume  \
84940  2025-02-28 15:40:00  83733.00  83868.00  83708.01  83865.99  54.82723   
84941  2025-02-28 15:41:00  83866.50  83938.48  83820.75  83833.42  43.24865   
84942  2025-02-28 15:42:00  83833.43  83874.86  83766.18  83808.49  51.09488   
84943  2025-02-28 15:43:00  83808.50  83840.00  83754.71  83756.72  35.85730   
84944  2025-02-28 15:44:00  83756.71  83859.99  83734.92  83744.00  47.66432   
84945  2025-02-28 15:45:00  83744.01  84000.00  83730.00  84000.00  54.75328   
84946  2025-02-28 15:46:00  84000.00  84049.49  83837.79  84000.00  65.56514   
84947  2025-02-28 15:47:00  83999.99  84083.77  83851.31  83867.05  42.53231   
84948  2025-02-28 15:48:00  83867.91  83966.88  83805.66  83867.80  57.18749   
84949  2025-02-28 15:49:00  83867.81  83905.28  83778.87  83900.00  47.55925   
84950  2025-02-28 15:50:00  83900.00  84072.55  83872.77  84018.86  45.22223   
84951  2025-02-28 15:51:00  84020.43  84221.96  83981.86  84179.11  42.70569   
84952  2025-02-28 15:52:00  84179.10  84204.96  84040.01  84060.77  44.19926   
84953  2025-02-28 15:53:00  84060.70  84123.21  84022.06  84046.20  28.58200   
84954  2025-02-28 15:54:00  84046.21  84169.82  84002.55  84002.56  53.24304   
84955  2025-02-28 15:55:00  84002.56  84002.56  83862.54  83879.53  48.18082   
84956  2025-02-28 15:56:00  83879.52  83912.49  83800.00  83800.01  61.60958   
84957  2025-02-28 15:57:00  83800.01  83888.29  83768.53  83849.54  46.47085   
84958  2025-02-28 15:58:00  83849.54  83947.75  83849.54  83947.75  30.48454   
84959  2025-02-28 15:59:00  83947.75  84046.57  83942.84  84005.05  25.85184   
84960  2025-02-28 16:00:00  84005.05  84037.04  83913.68  83940.96  64.74482   

       Number of Trades Coin        MACD  MACD_Signal  MACD_Hist        RSI  
84940              9879  BTC  167.735239   254.670668 -86.935429  54.301666  
84941              7348  BTC  148.317707   233.400076 -85.082369  53.152878  
84942              8433  BTC  129.425593   212.605179 -83.179586  52.241844  
84943              3967  BTC  109.019342   191.888012 -82.868669  50.313294  
84944              7445  BTC   90.774453   171.665300 -80.890847  49.826587  
84945              8939  BTC   95.867210   156.505682 -60.638472  58.522822  
84946             11988  BTC   98.764758   144.957497 -46.192739  58.522822  
84947              8717  BTC   89.303694   133.826736 -44.523043  52.990893  
84948             10021  BTC   80.933303   123.248050 -42.314747  53.017873  
84949              7615  BTC   76.021648   113.802769 -37.781121  54.232372  
84950             10815  BTC   80.788851   107.199986 -26.411134  58.497245  
84951              8746  BTC   96.386645   105.037318  -8.650673  63.443327  
84952              8191  BTC   98.068487   103.643551  -5.575064  57.950917  
84953              6646  BTC   97.106301   102.336101  -5.229800  57.293270  
84954              8422  BTC   91.764573   100.221796  -8.457222  55.270097  
84955              8341  BTC   76.719350    95.521307 -18.801957  49.918294  
84956              7231  BTC   57.714012    87.959848 -30.245836  46.766248  
84957              7604  BTC   46.117191    79.591316 -33.474126  48.929368  
84958              6875  BTC   44.340226    72.541098 -28.200872  53.006920  
84959              6521  BTC   47.013656    67.435610 -20.421954  55.251772  
84960              9705  BTC   43.459863    62.640460 -19.180598  52.245534